In [ ]:
#| default_exp cameras

# OpenHSI Hardware Camera Implementations

:::{.callout-tip}

This module can be imported using `from openhsi.cameras import *`

:::

Wrapper class and example code for getting images from the OpenHSI.

:::{.callout-tip}

To use the camera, you will need some calibration files. You can also generate these files following this [guide](https://openhsi.github.io/openhsi/tutorial_calibrate.html) which uses the [`calibrate` module](https://openhsi.github.io/openhsi/calibrate.html).

:::

In [ ]:
#| hide

# documentation extraction for class methods
from nbdev.showdoc import *

# unit tests using test_eq(...)
from fastcore.test import *

# monkey patching class methods using @patch
from fastcore.foundation import *
from fastcore.foundation import patch

# imitation of Julia's multiple dispatch using @typedispatch
from fastcore.dispatch import typedispatch

# bring forth **kwargs from an inherited class for documentation
from fastcore.meta import delegates

# external
import numpy as np
import ctypes
import matplotlib.pyplot as plt
import warnings
from tqdm import tqdm
from functools import partial

# internal
from openhsi.capture import OpenHSI
from openhsi.shared import SharedOpenHSI

## FLIR 

Follow the install instructions for [https://pypi.org/project/simple-pyspin/](https://pypi.org/project/simple-pyspin/). This includes the Spinnaker SDK and the Python pyspin .whl file from [https://flir.app.boxcn.net/v/SpinnakerSDK](https://flir.app.boxcn.net/v/SpinnakerSDK). 

:::{.callout-note}

PySpin only supports Python2.7/3.6-3.8

:::

There are some additional settings:
- `win_resolution`: size of area on detector to readout (width, height)
- `win_offset`: offsets (x,y) from edge of detector for a selective 
- `exposure_us`: is the camera exposure time to use in microseconds

In [ ]:
#| export cameras

@delegates()
class FlirCameraBase():
    """Interface for FLIR camera"""
    
    def __init__(self, **kwargs):
        """Initialise FLIR camera"""
        super().__init__(**kwargs)
        
        from simple_pyspin import Camera
        
        self.flircam = Camera()
        self.flircam.init()
        self.flircam.GainAuto = 'Off'
        self.flircam.Gain = 0
        self.flircam.AcquisitionFrameRateAuto = 'Off'
        self.flircam.AcquisitionFrameRateEnabled = True
        self.flircam.AcquisitionFrameRate = int( min(1_000/(self.settings["exposure_ms"]+1),120) )
    
        self.flircam.ExposureAuto = 'Off'
        self.flircam.ExposureTime = self.settings["exposure_ms"]*1e3 # convert to us
        self.flircam.GammaEnabled = False
        
        self.flircam.Width = self.flircam.SensorWidth if self.settings["win_resolution"][1] == 0 else self.settings["win_resolution"][1]
        self.flircam.Height = self.flircam.SensorHeight if self.settings["win_resolution"][0] == 0 else self.settings["win_resolution"][0]
        self.flircam.OffsetY, self.flircam.OffsetX = self.settings["win_offset"]

    
    def start_cam(self):
        self.flircam.start()
    
    def stop_cam(self):
        self.flircam.stop()
        
    def __close__(self):
        self.flircam.close()
    
    def get_img(self) -> np.ndarray:
        return self.flircam.get_array()
    
    def get_temp(self) -> float:
        return self.flircam.DeviceTemperature
    
    def set_exposure(self, exposure_ms:float):
        """sets the FLIR camera exposure time to `exposure_ms`."""

        if exposure_ms < self.flircam.ExposureMinAbsVal_Float/1000:
            exposure_ms = self.flircam.ExposureMinAbsVal_Float/1000

        self.settings["exposure_ms"] = exposure_ms
        
        self.flircam.AcquisitionFrameRateAuto = 'Off'
        self.flircam.AcquisitionFrameRateEnabled = True
        self.flircam.AcquisitionFrameRate = int( min(1_000/(self.settings["exposure_ms"]+1),120) )
        self.flircam.ExposureAuto = 'Off'

        self.flircam.ExposureTime = self.settings["exposure_ms"]*1e3 # convert to us
        
@delegates()
class FlirCamera(FlirCameraBase, OpenHSI):
    pass

In [ ]:
#| hardware

json_path='../assets/cam_settings_flir.json'
cal_path='../assets/cam_calibration_flir.pkl'

with FlirCamera(n_lines=1000, 
                 processing_lvl = 2, 
                 cal_path=cal_path,json_path=json_path,
                ) as cam:
    cam.collect()
    fig = cam.show(hist_eq=True)
    
fig

100%|██████████| 1000/1000 [00:12<00:00, 78.71it/s]


:RGB   [x,y]   (R,G,B)

### Multiprocessing camera export

Export cameras using the SharedOpenHSI class.

In [ ]:
#| export cameras
        
@delegates()
class SharedFlirCamera(FlirCameraBase, SharedOpenHSI):
    pass